In [16]:
from google.cloud import bigquery
from google.oauth2 import service_account

import pandas as pd
import plotly.express as px
from pandasql import sqldf

In [17]:
credentials = service_account.Credentials.from_service_account_file(r"C:\Users\Chase\Downloads\used-car-summer-2023-project-b4807c4731d7.json")

bigquery_client = bigquery.Client(credentials=credentials, project='used-car-summer-2023-project')

### **EDA Results**
##### 1. Exclude All Listings Over $50,000
##### 2. Exclude All Listings Before 2010
##### 3. Exclude All Listings with Mileage Over 130,000
##### 4. Exclude the Following Makes: Rivian, Polestar, Saab, Freightliner, Saturn, Suzuki, smart, Mercury, Lamborghini, McLaren, Ferrari, Pontiac, Rolls-Royce, HUMMER, Bentley, Maserati, FIAT, Genesis, Scion, Jaguar
##### 5. Exclude All Listings with the Following Exterior Colors: Beige, Teal, Copper, Maroon, Yellow, Purple
##### 6. Exclude All Listings with the Following Interior Colors: Pink, Purple, Yellow, Green, Orange, Blue
##### 7. Exclude All Models with Less Than 50 Occurrences
##### 8. Exclude All Listings with More Than 3 Accidents
##### 9. Exclude All Listings with More Than 5 Owners

In [18]:
query = bigquery_client.query('SELECT * FROM `training_data.wrangled_training_data`').result()

wrangled_data = query.to_dataframe()
wrangled_data

price  year       make    model                              trim   
0        3795  1997      Honda     CR-V                                    \
1       16880  1997  Chevrolet   Malibu                                LS   
2       12000  1997    Porsche  Boxster                            Manual   
3       12495  1997      Buick  Riviera                         Coupe 3.8   
4       15590  1997  Chevrolet   Camaro                        Z/28 Coupe   
...       ...   ...        ...      ...                               ...   
128406  75518  2024     Toyota   Tundra    1794 Edition CrewMax 5.5' Bed    
128407  73568  2024     Toyota   Tundra  Hybrid Limited CrewMax 5.5' Bed    
128408  75268  2024     Toyota   Tundra  Hybrid Limited CrewMax 5.5' Bed    
128409  87289  2024     Toyota   Tundra  Hybrid TRD Pro CrewMax 5.5' Bed    
128410  87289  2024     Toyota   Tundra  Hybrid TRD Pro CrewMax 5.5' Bed    

        mileage exterior_color interior_color  num_accidents  num_owners   
0        153629           Blue           Gray              0         6.0  \
1         14506          Green           Gray              0         5.0   
2         90208         Silver            Red              1        10.0   
3        129768          White          Beige              1         7.0   
4         64249          White          White              0         3.0   
...         ...            ...            ...            ...         ...   
128406        5          White          Beige              0         0.0   
128407        5          Black          Black              0         0.0   
128408        5          White          Black              0         0.0   
128409        5          Brown          Black              0         0.0   
128410        5          White          Black              0         0.0   

       usage_type          city state  
0        Personal     Englewood    CO  
1        Personal  Grand island    NE  
2        Personal    Scottsdale    AZ  
3           Fleet          Mesa    AZ  
4        Personal      Lakewood    CO  
...           ...           ...   ...  
128406   Personal      Prescott    AZ  
128407   Personal      Prescott    AZ  
128408   Personal      Prescott    AZ  
128409   Personal      Prescott    AZ  
128410   Personal      Prescott    AZ  

[128411 rows x 13 columns]

In [19]:
wrangled_data['year'] = wrangled_data['year'].astype(int)
wrangled_data['price'] = wrangled_data['price'].astype(int)

In [20]:
# Exclude all listings with a price over 50000
staged_data = wrangled_data.query('price < 49000 & price >= 8000')
# Exclude all listings with a model_year before 2010
staged_data = staged_data.query('year >= 2011 & year != 2024')
# Exclude all listings with a mileage over 130000
staged_data = staged_data.query('mileage < 128000')
# Exclude all listings with an unqualified exterior_color
staged_data = staged_data[~staged_data['exterior_color'].isin(['Beige', 'Teal', 'Copper', 'Maroon', 'Yellow', 'Purple'])]
# Exclude all listings with an unqualified interior_color
staged_data['interior_color'] = staged_data['interior_color'].str.strip()
staged_data = staged_data[~staged_data['interior_color'].isin(['Pink', 'Purple', 'Yellow', 'Green', 'Orange', 'Blue'])]
# Exclude all listings with num_accidents over 3
staged_data = staged_data.query('num_accidents <= 3')
# Exclude all listings with num_owners over 5
staged_data = staged_data.query('num_owners <= 5')
staged_data = sqldf("SELECT * FROM staged_data WHERE num_owners = 0 AND year >= 2021 OR num_owners > 0")
staged_data.reset_index(drop=True, inplace=True)
staged_data

C:\Users\Chase\AppData\Local\Temp\ipykernel_30420\2500162970.py:6: RuntimeWarning: Engine has switched to 'python' because numexpr does not support extension array dtypes. Please set your engine to python manually.
  staged_data = staged_data.query('mileage < 128000')
C:\Users\Chase\AppData\Local\Temp\ipykernel_30420\2500162970.py:13: RuntimeWarning: Engine has switched to 'python' because numexpr does not support extension array dtypes. Please set your engine to python manually.
  staged_data = staged_data.query('num_accidents <= 3')


price  year      make   model   
0       13995  2011     Acura     MDX  \
1       14998  2011     Acura     RDX   
2        8895  2011  Chrysler     300   
3       16998  2011     Acura     MDX   
4       14999  2011  Chrysler     300   
...       ...   ...       ...     ...   
113399  44998  2023    Toyota  Tacoma   
113400  46500  2023    Toyota  Tacoma   
113401  44900  2023    Toyota  Tacoma   
113402  44998  2023    Toyota  Tacoma   
113403  44998  2023    Toyota  Tacoma   

                                                 trim  mileage exterior_color   
0                                                        91307           Gray  \
1                                                        92911           Gray   
2                                                       118636         Silver   
3                                                        97480           Blue   
4                                                        54677          Black   
...                                               ...      ...            ...   
113399  Trail Edition Double Cab 5' Bed V6  Automatic     9485          White   
113400  Trail Edition Double Cab 5' Bed V6  Automatic     1080           Gray   
113401  Trail Edition Double Cab 5' Bed V6  Automatic      737           Gray   
113402  Trail Edition Double Cab 5' Bed V6  Automatic     7980          White   
113403  Trail Edition Double Cab 5' Bed V6  Automatic     7783          White   

       interior_color  num_accidents  num_owners usage_type            city   
0             Unknown              0         2.0   Personal            Mesa  \
1                Gray              2         2.0   Personal  South Portland   
2               Black              1         3.0   Personal          Fresno   
3                Gray              2         2.0   Personal         Danvers   
4               Black              0         3.0   Personal            Mesa   
...               ...            ...         ...        ...             ...   
113399          Black              0         1.0   Personal      Sacramento   
113400          Black              0         1.0   Personal     Albuquerque   
113401          Black              0         1.0   Personal          Aurora   
113402          Black              0         1.0   Personal          Oxnard   
113403          Black              0         1.0   Personal      Costa Mesa   

       state  
0         AZ  
1         ME  
2         CA  
3         MA  
4         AZ  
...      ...  
113399    CA  
113400    NM  
113401    CO  
113402    CA  
113403    CA  

[113404 rows x 13 columns]

In [21]:
unqualified_models = sqldf("SELECT make || ' ' || model AS model, COUNT(*) AS num_listings FROM wrangled_data GROUP BY model HAVING num_listings < 50")
staged_data['merged'] = staged_data['make'] + ' ' + staged_data['model']
staged_data = sqldf("SELECT * FROM staged_data WHERE merged NOT IN(SELECT DISTINCT model FROM unqualified_models)")
staged_data

price  year      make   model   
0       13995  2011     Acura     MDX  \
1       14998  2011     Acura     RDX   
2        8895  2011  Chrysler     300   
3       16998  2011     Acura     MDX   
4       14999  2011  Chrysler     300   
...       ...   ...       ...     ...   
111315  44998  2023    Toyota  Tacoma   
111316  46500  2023    Toyota  Tacoma   
111317  44900  2023    Toyota  Tacoma   
111318  44998  2023    Toyota  Tacoma   
111319  44998  2023    Toyota  Tacoma   

                                                 trim  mileage exterior_color   
0                                                        91307           Gray  \
1                                                        92911           Gray   
2                                                       118636         Silver   
3                                                        97480           Blue   
4                                                        54677          Black   
...                                               ...      ...            ...   
111315  Trail Edition Double Cab 5' Bed V6  Automatic     9485          White   
111316  Trail Edition Double Cab 5' Bed V6  Automatic     1080           Gray   
111317  Trail Edition Double Cab 5' Bed V6  Automatic      737           Gray   
111318  Trail Edition Double Cab 5' Bed V6  Automatic     7980          White   
111319  Trail Edition Double Cab 5' Bed V6  Automatic     7783          White   

       interior_color  num_accidents  num_owners usage_type            city   
0             Unknown              0         2.0   Personal            Mesa  \
1                Gray              2         2.0   Personal  South Portland   
2               Black              1         3.0   Personal          Fresno   
3                Gray              2         2.0   Personal         Danvers   
4               Black              0         3.0   Personal            Mesa   
...               ...            ...         ...        ...             ...   
111315          Black              0         1.0   Personal      Sacramento   
111316          Black              0         1.0   Personal     Albuquerque   
111317          Black              0         1.0   Personal          Aurora   
111318          Black              0         1.0   Personal          Oxnard   
111319          Black              0         1.0   Personal      Costa Mesa   

       state         merged  
0         AZ      Acura MDX  
1         ME      Acura RDX  
2         CA   Chrysler 300  
3         MA      Acura MDX  
4         AZ   Chrysler 300  
...      ...            ...  
111315    CA  Toyota Tacoma  
111316    NM  Toyota Tacoma  
111317    CO  Toyota Tacoma  
111318    CA  Toyota Tacoma  
111319    CA  Toyota Tacoma  

[111320 rows x 14 columns]

## **Post-Processing EDA**

In [22]:
pd.set_option('display.float_format', lambda x: '%.2f' % x)
staged_data.describe()

price      year   mileage  num_accidents  num_owners
count 111320.00 111320.00 111320.00      111320.00   111320.00
mean   26354.59   2018.44  52332.99           0.32        1.59
std     8593.13      2.74  30501.27           0.60        0.81
min     8000.00   2011.00      5.00           0.00        0.00
25%    19998.00   2017.00  28715.00           0.00        1.00
50%    24998.00   2019.00  47763.50           0.00        1.00
75%    31998.00   2020.00  73233.50           1.00        2.00
max    48999.00   2023.00 127998.00           3.00        5.00

In [23]:
fig = px.histogram(staged_data['price'], nbins=50)
fig.update_layout(xaxis=dict(showgrid=False), yaxis=dict(showgrid=False), title='Price Distribution')

In [24]:
fig = px.histogram(staged_data['year'])
fig.update_layout(xaxis=dict(showgrid=False), yaxis=dict(showgrid=False), title='Model Year Distribution')

In [25]:
fig = px.histogram(staged_data['mileage'], nbins=100)
fig.update_layout(xaxis=dict(showgrid=False), yaxis=dict(showgrid=False), title='Mileage Distribution')

In [26]:
listings_by_make = sqldf("SELECT make, COUNT(*) num_listings FROM staged_data GROUP BY make")

fig = px.bar(listings_by_make, listings_by_make['make'], listings_by_make['num_listings'], text_auto=True, title="Listings by Make", height=550)
fig.update_yaxes(showgrid=False)
fig.update_traces(textfont_size=12, textangle=0, textposition="outside")
fig.update_layout(xaxis={'categoryorder':'total descending'})
fig.show()

In [27]:
listings_by_ext = sqldf("SELECT exterior_color, COUNT(*) num_listings FROM staged_data GROUP BY exterior_color")

fig = px.bar(listings_by_ext, listings_by_ext['exterior_color'], listings_by_ext['num_listings'], text_auto=True, title="Listings by Exterior Color", height=550)
fig.update_yaxes(showgrid=False)
fig.update_traces(textfont_size=12, textangle=0, textposition="outside")
fig.update_layout(xaxis={'categoryorder':'total descending'})
fig.show()

In [28]:
listings_by_int = sqldf("SELECT interior_color, COUNT(*) num_listings FROM staged_data GROUP BY interior_color")

fig = px.bar(listings_by_int, listings_by_int['interior_color'], listings_by_int['num_listings'], text_auto=True, title="Listings by Interior Color", height=550)
fig.update_yaxes(showgrid=False)
fig.update_traces(textfont_size=12, textangle=0, textposition="outside")
fig.update_layout(xaxis={'categoryorder':'total descending'})
fig.show()

In [29]:
listings_by_accidents = sqldf("SELECT num_accidents, COUNT(*) num_listings FROM staged_data GROUP BY num_accidents")

fig = px.bar(listings_by_accidents, listings_by_accidents['num_accidents'], listings_by_accidents['num_listings'], text_auto=True, title="Listings by # of Accidents", height=550)
fig.update_yaxes(showgrid=False)
fig.update_traces(textfont_size=12, textangle=0, textposition="outside")
fig.update_layout(xaxis={'categoryorder':'total descending'})
fig.show()

In [30]:
listings_by_owners = sqldf("SELECT num_owners, COUNT(*) num_listings FROM staged_data GROUP BY num_owners")

fig = px.bar(listings_by_owners, listings_by_owners['num_owners'], listings_by_owners['num_listings'], text_auto=True, title="Listings by # of Owners", height=550)
fig.update_yaxes(showgrid=False)
fig.update_traces(textfont_size=12, textangle=0, textposition="outside")
fig.update_layout(xaxis={'categoryorder':'total descending'})
fig.show()

In [32]:
import pandas_gbq
wrangled_listings = staged_data
pandas_gbq.to_gbq(wrangled_listings, 'used-car-summer-2023-project.training_data.final_training_data', project_id='used-car-summer-2023-project', if_exists='replace')

100%|██████████| 1/1 [00:00<?, ?it/s]
